In [464]:
from bs4 import BeautifulSoup
import pandas as pd
import requests
import json
import re
from scipy import stats

In [426]:
all_data = []
#iterates through years of available Henley data
for num in range(1999,2025):
  print(num)
  #retrieves data from url of appropriate year
  url = f'https://www.hrr.co.uk/results/?race-year={num}'
  initial_r = requests.get(url)
  initial_soup = BeautifulSoup(initial_r.text, "html.parser")

  #converts to soup and finds number of last page
  pages_string = initial_soup.find_all("historical-results")[0]['initial-pagination']
  print(pages_string)

  # Convert the string into a dictionary
  pages_dict = json.loads(pages_string)

  # Access the 'lastPage' value
  last_page = pages_dict.get('lastPage')
  print(last_page)
  yearly_data = []
  for page in range(1,last_page + 1):
    #loads url with results for each page
    url = f'https://www.hrr.co.uk/results/?race-year={num}&result-page={page}'
    r = requests.get(url)

    #converts into bs object and finds results table
    soup = BeautifulSoup(r.text, "html.parser")
    #print(soup)
    results_data = soup.find_all("historical-results")[0]['initial-results']

    #converts results into json and append
    results_json = json.loads(results_data)
    yearly_data.extend(results_json)

  #adds yearly data to all data
  print(yearly_data)
  if(yearly_data):
    all_data.append(yearly_data)

1999
{"firstPage":1,"nextPage":2,"lastPage":15,"previousPage":1,"currentPage":1,"totalPages":15,"smartPages":[1,2,3,4,5,"\u2026",15]}
15
[{'id': 17047, 'number': '', 'trophy': {'id': 195, 'name': 'The Britannia Challenge Cup', 'slug': 'the-britannia-challenge-cup', 'shortName': 'Britannia', 'extraShortName': 'Britannia', 'class': {'id': 196, 'name': 'M4+'}}, 'round': 'FINAL', 'winner': {'name': 'Molesey Boat Club', 'shortName': 'Molesey B.C.'}, 'loser': {'name': 'Isis Boat Club', 'shortName': 'Isis B.C.'}, 'withdrawn': False, 'station': '2 - Bucks', 'barrier': {'split': '2:08', 'newRecord': False, 'equalsRecord': False, 'loserLeading': False}, 'fawley': {'split': '3:36', 'newRecord': False, 'equalsRecord': False, 'loserLeading': False}, 'finish': {'split': '7:19', 'newRecord': False, 'equalsRecord': False}, 'verdict': '1 Length', 'raceDateTime': '1999-07-04T00:00:00+00:00', 'raceDay': 'Sunday', 'raceYear': '1999', 'raceTime': '00:00'}, {'id': 17642, 'number': '', 'trophy': {'id': 197, 

In [427]:
#convert json data into df
df = pd.DataFrame()
for i in range(len(all_data)):
  year_df = pd.json_normalize(all_data[i])
  dfs = [df,year_df]
  df = pd.concat(dfs)

In [428]:
df

id number  round  withdrawn    station     verdict  \
0    17047         FINAL      False  2 - Bucks    1 Length   
1    17642         FINAL      False  1 - Berks  4¾ Lengths   
2    18341         FINAL      False  1 - Berks   3 Lengths   
3    18853         FINAL      False  2 - Bucks  2¼ Lengths   
4    19513         FINAL      False  1 - Berks    ½ Length   
..     ...    ...    ...        ...        ...         ...   
403  46436      5  heats      False  2 - Bucks   2 lengths   
404  46435      4  heats      False  2 - Bucks    ¾ length   
405  46432      3  heats      False  2 - Bucks  2 ¾ length   
406  46431      2  heats      False  1 - Berks  2 ¼ length   
407  46430      1  heats      False  1 - Berks   5 lengths   

                  raceDateTime  raceDay raceYear raceTime  trophy.id  \
0    1999-07-04T00:00:00+00:00   Sunday     1999    00:00        195   
1    1999-07-04T00:00:00+00:00   Sunday     1999    00:00        197   
2    1999-07-04T00:00:00+00:00   Sunday     1999    00:00        201   
3    1999-07-04T00:00:00+00:00   Sunday     1999    00:00        203   
4    1999-07-04T00:00:00+00:00   Sunday     1999    00:00        205   
..                         ...      ...      ...      ...        ...   
403  2024-07-02T08:20:00+00:00  Tuesday     2024    08:20        195   
404  2024-07-02T08:15:00+00:00  Tuesday     2024    08:15        245   
405  2024-07-02T08:10:00+00:00  Tuesday     2024    08:10        222   
406  2024-07-02T08:05:00+00:00  Tuesday     2024    08:05        235   
407  2024-07-02T08:00:00+00:00  Tuesday     2024    08:00        203   

                              trophy.name  \
0             The Britannia Challenge Cup   
1            The Diamond Challenge Sculls   
2         The Double Sculls Challenge Cup   
3                The Fawley Challenge Cup   
4                 The Grand Challenge Cup   
..                                    ...   
403           The Britannia Challenge Cup   
404              The Wyfold Challenge Cup   
405  The Princess Elizabeth Challenge Cup   
406              The Temple Challenge Cup   
407              The Fawley Challenge Cup   

                              trophy.slug trophy.shortName  \
0             the-britannia-challenge-cup        Britannia   
1            the-diamond-challenge-sculls         Diamonds   
2         the-double-sculls-challenge-cup          Doubles   
3                the-fawley-challenge-cup           Fawley   
4                 the-grand-challenge-cup            Grand   
..                                    ...              ...   
403           the-britannia-challenge-cup        Britannia   
404              the-wyfold-challenge-cup           Wyfold   
405  the-princess-elizabeth-challenge-cup               PE   
406              the-temple-challenge-cup           Temple   
407              the-fawley-challenge-cup           Fawley   

    trophy.extraShortName  trophy.class.id trophy.class.name  \
0               Britannia              196               M4+   
1                Diamonds              574                M1   
2                 Doubles              573                M2   
3                  Fawley              571                M4   
4                   Grand              206               M8+   
..                    ...              ...               ...   
403             Britannia              196               M4+   
404                Wyfold              571                M4   
405                    PE              206               M8+   
406                Temple              206               M8+   
407                Fawley              571                M4   

                                           winner.name  \
0                                    Molesey Boat Club   
1              M. Hacker, Ruderclub Magdeburg, Germany   
2    I.M. McGowan & N.V. Peterson, Augusta Sculling...   
3                         Leander Club & Tiffin School   
4    Ruder Club Hansa Von 1898 e.V. Dortmud & Berli..

In [429]:
#display data with full columns
pd.set_option('display.max_columns', None)
df['raceDateTime'] = pd.to_datetime(df['raceDateTime'])

In [430]:
df.to_csv('henley_1999_2024.csv',index=False)

## Analysis

In [431]:
stats_df_berks = pd.DataFrame({
    'N_races': [],
    'Berks_wins': [],
    'Statistic': [],
    'p_value': []
},index=[])

stats_df_intl = pd.DataFrame({
    'N_races': [],
    'International_on_bucks': [],
    'Statistic': [],
    'p_value': []
},index=[])

In [432]:
def berks_binom_test(dataframe,prob=0.5):
  berks_win_num = len(dataframe[dataframe['station'] == '1 - Berks'])
  race_num = len(dataframe)

  # number of trials (races)
  n = race_num

  # number of successes (berks wins)
  k = berks_win_num

  # expected probability of success if stations are fair
  p = prob

  # perform the test
  p_value = stats.binomtest(k, n, p, alternative='greater')
  return(p_value)

In [433]:
def append_to_berks(p,name):
    global stats_df_berks
    new_df= pd.DataFrame({'N_races': p.n, 'Berks_wins': p.k, 'Statistic': p.statistic, 'p_value': p.pvalue}, index=[name])
    stats_df_berks = pd.concat([stats_df_berks,new_df])

def append_to_intl(p,name):
    global stats_df_intl
    new_df= pd.DataFrame({'N_races': p.n, 'International_on_bucks': p.k, 'Statistic': p.statistic, 'p_value': p.pvalue}, index=[name])
    stats_df_intl = pd.concat([stats_df_intl,new_df])

In [434]:
p = berks_binom_test(df)
print('p-value:', p)
append_to_berks(p,'all_races')


p-value: BinomTestResult(k=4044, n=7556, alternative='greater', statistic=0.5352038115404976, pvalue=4.945864025542424e-10)


In [435]:
stats_df_berks

N_races  Berks_wins  Statistic       p_value
all_races   7556.0      4044.0   0.535204  4.945864e-10

These results show that (assuming the lanes are randomly decided, i.e. no stronger crew is placed in one lane vs the other, that the Berks station has a statistically significant advantage)

## More Detailed Analysis

In [436]:
countries = [
    "Afghanistan", "Albania", "Algeria", "Andorra", "Angola",
    "Antigua and Barbuda", "Argentina", "Armenia", "Australia",
    "Austria", "Azerbaijan", "Bahamas", "Bahrain", "Bangladesh",
    "Barbados", "Belarus", "Belgium", "Belize", "Benin", "Bhutan",
    "Bolivia", "Bosnia and Herzegovina", "Botswana", "Brazil",
    "Brunei Darussalam", "Bulgaria", "Burkina Faso", "Burundi",
    "Côte d'Ivoire", "Cabo Verde", "Cambodia", "Cameroon", "Canada",
    "Central African Republic", "Chad", "Chile", "China", "Colombia",
    "Comoros", "Congo", "Costa Rica", "Croatia", "Cuba", "Cyprus",
    "Czech Republic", "Democratic People's Republic of Korea",
    "Democratic Republic of the Congo", "Denmark", "Djibouti",
    "Dominica", "Dominican Republic", "Ecuador", "Egypt",
    "El Salvador", "Equatorial Guinea", "Eritrea", "Estonia",
    "Eswatini", "Ethiopia", "Fiji", "Finland", "France", "Gabon",
    "Gambia", "Georgia", "Germany", "Ghana", "Greece", "Grenada",
    "Guatemala", "Guinea", "Guinea Bissau", "Guyana", "Haiti",
    "Honduras", "Hungary", "Iceland", "India", "Indonesia",
    "Iran", "Iraq", "Ireland", "Israel", "Italy", "Jamaica",
    "Japan", "Jordan", "Kazakhstan", "Kenya", "Kiribati",
    "Kuwait", "Kyrgyzstan", "Lao People’s Democratic Republic",
    "Latvia", "Lebanon", "Lesotho", "Liberia", "Libya", "Liechtenstein",
    "Lithuania", "Luxembourg", "Madagascar", "Malawi", "Malaysia",
    "Maldives", "Mali", "Malta", "Marshall Islands", "Mauritania",
    "Mauritius", "Mexico", "Micronesia", "Monaco", "Mongolia",
    "Montenegro", "Morocco", "Mozambique", "Myanmar", "Namibia",
    "Nauru", "Nepal", "Netherlands", "New Zealand", "Nicaragua",
    "Niger","Nigeria", "North Macedonia", "Norway", "Oman",
    "Pakistan", "Palau", "Panama", "Papua New Guinea", "Paraguay",
    "Peru", "Philippines", "Poland", "Portugal", "Qatar", "Republic of Korea",
    "Republic of Moldova", "Romania", "Russian Federation", "Rwanda",
    "Saint Kitts and Nevis", "Saint Lucia", "Saint Vincent and the Grenadines",
    "Samoa", "San Marino", "Sao Tome and Principe", "Saudi Arabia",
    "Senegal", "Serbia", "Seychelles", "Sierra Leone", "Singapore",
    "Slovakia", "Slovenia", "Solomon Islands", "Somalia", "South Africa",
    "South Sudan", "Spain", "Sri Lanka", "Sudan", "Suriname",
    "Sweden", "Switzerland", "Syrian Arab Republic", "Tajikistan",
    "Thailand", "Timor-Leste", "Togo", "Tonga", "Trinidad and Tobago",
    "Tunisia", "Turkey", "Turkmenistan", "Tuvalu", "Uganda",
    "Ukraine", "United Arab Emirates", "United Kingdom of Great Britain and Northern Ireland",
    "United Republic of Tanzania", "United States of America", "U.S.A.", "America" "Uruguay",
    "Uzbekistan", "Vanuatu", "Venezuela", "Vietnam", "Yemen",
    "Zambia", "Zimbabwe"
]

In [437]:
#races featuring an international vs uk crew
# Join the strings in the list with the OR operator for regex
country_pattern = '|'.join(countries)

# Get a boolean mask of rows where the column contains any of the strings in preset_list
mask1 = df['winner.name'].str.contains(country_pattern)
mask2 = df['loser.name'].str.contains(country_pattern)
mask3 = ~df['winner.name'].str.contains(country_pattern)
mask4 = ~df['loser.name'].str.contains(country_pattern)

# Use the mask to get the rows
international_v_uk_df = df[(mask1 | mask2) & (mask3 | mask4)]

In [438]:
def international_on_bucks_test(dataframe,prob=0.5,pattern=country_pattern):
  
  #these masks as applied here find all instances where intl crew is on Bucks, win or lose
  mask1 = dataframe['winner.name'].str.contains(pattern)
  mask2 = dataframe['station'] == '2 - Bucks'
  mask3 = dataframe['loser.name'].str.contains(pattern)
  mask4 = dataframe['station'] == '1 - Berks'

  intl_on_bucks_df = dataframe[(mask1 & mask2) | (mask3 & mask4)]

  intl_on_berks_num = len(intl_on_bucks_df)
  race_num = len(dataframe)

  # number of trials (races)
  n = race_num

  # number of successes (berks placements)
  k = intl_on_berks_num

  # expected probability of intl vs uk crew being assigned a station (i.e. .5)
  p = prob

  # perform the test
  p_value = stats.binomtest(k, n, p, alternative='greater')
  return(p_value)

In [439]:
p = international_on_bucks_test(international_v_uk_df)
print('p-value:', p)
append_to_intl(p,"all_international_v_uk_races")

p-value: BinomTestResult(k=1530, n=2985, alternative='greater', statistic=0.5125628140703518, pvalue=0.08779310150216048)


In [440]:
p = berks_binom_test(international_v_uk_df)
print('p-value:', p)
append_to_berks(p,"all_international_v_uk_races")

p-value: BinomTestResult(k=1542, n=2985, alternative='greater', statistic=0.5165829145728643, pvalue=0.03642031333599513)


## Weekend Analysis

In [441]:
#races featuring an international vs uk crew on the weekend
weekend = ['Saturday','Sunday']
weekend_pattern = '|'.join(weekend)

mask1 = international_v_uk_df['raceDay'].str.contains(weekend_pattern)

weekend_international_v_uk_df = international_v_uk_df[mask1]

In [442]:
p = international_on_bucks_test(weekend_international_v_uk_df)
append_to_intl(p,"weekend_international_v_uk_races")

In [443]:
p = berks_binom_test(weekend_international_v_uk_df)
print('p-value:', p)
append_to_berks(p,"weekend_international_v_uk_races")

p-value: BinomTestResult(k=355, n=672, alternative='greater', statistic=0.5282738095238095, pvalue=0.07671943059079347)


In [444]:
#all races on the weekend
weekend = ['Saturday','Sunday']
weekend_pattern = '|'.join(weekend)

mask1 = df['raceDay'].str.contains(weekend_pattern)

weekend_df = df[mask1]
p = berks_binom_test(weekend_df)
print('p-value:', p)
append_to_berks(p,"all_weekend_races")

p-value: BinomTestResult(k=863, n=1548, alternative='greater', statistic=0.5574935400516796, pvalue=3.3439138271073713e-06)


## Year by Year Analysis

In [445]:
years = list(range(1999, 2025))
years.remove(2020)

for year in years:
    year_df = df[df['raceDateTime'].dt.year == year]
    intl_year_df = international_v_uk_df[international_v_uk_df['raceDateTime'].dt.year == year]
    print(f"Year: {year}")
    p1 = berks_binom_test(year_df)
    append_to_berks(p1,year)
    print(f"Berks Winning: {p1}")
    p2 = international_on_bucks_test(intl_year_df)
    append_to_intl(p2,year)
    print(f"International Crew on Bucks: {p2}")
    print("----------------")
    print("----------------")
    print('\n')

Year: 1999
Berks Winning: BinomTestResult(k=163, n=284, alternative='greater', statistic=0.573943661971831, pvalue=0.007416341299066738)
International Crew on Bucks: BinomTestResult(k=60, n=114, alternative='greater', statistic=0.5263157894736842, pvalue=0.3198846843214754)
----------------
----------------


Year: 2000
Berks Winning: BinomTestResult(k=156, n=285, alternative='greater', statistic=0.5473684210526316, pvalue=0.061691871288749825)
International Crew on Bucks: BinomTestResult(k=49, n=92, alternative='greater', statistic=0.532608695652174, pvalue=0.3012061388480754)
----------------
----------------


Year: 2001
Berks Winning: BinomTestResult(k=165, n=281, alternative='greater', statistic=0.5871886120996441, pvalue=0.002054846008074714)
International Crew on Bucks: BinomTestResult(k=66, n=119, alternative='greater', statistic=0.5546218487394958, pvalue=0.13562416887970227)
----------------
----------------


Year: 2002
Berks Winning: BinomTestResult(k=149, n=269, alternativ

In [446]:
days = ["Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]

for day in days:
    day_df = df[df['raceDay'] == day]
    intl_day_df = international_v_uk_df[international_v_uk_df['raceDay'] == day]
    print(f"Year: {day}")
    p1 = berks_binom_test(day_df)
    append_to_berks(p1,day)
    print(f"Berks Winning: {p1}")
    p2 = international_on_bucks_test(intl_day_df)
    append_to_intl(p2,day)
    print(f"International Crew on Bucks: {p2}")
    print("----------------")
    print("----------------")
    print('\n')

Year: Tuesday
Berks Winning: BinomTestResult(k=134, n=242, alternative='greater', statistic=0.5537190082644629, pvalue=0.0539244323626138)
International Crew on Bucks: BinomTestResult(k=39, n=81, alternative='greater', statistic=0.48148148148148145, pvalue=0.6715037662068212)
----------------
----------------


Year: Wednesday
Berks Winning: BinomTestResult(k=1064, n=2022, alternative='greater', statistic=0.5262116716122651, pvalue=0.009758853050852426)
International Crew on Bucks: BinomTestResult(k=345, n=640, alternative='greater', statistic=0.5390625, pvalue=0.026336626041583048)
----------------
----------------


Year: Thursday
Berks Winning: BinomTestResult(k=1054, n=2035, alternative='greater', statistic=0.5179361179361179, pvalue=0.055225968397376965)
International Crew on Bucks: BinomTestResult(k=422, n=833, alternative='greater', statistic=0.5066026410564226, pvalue=0.364502689169866)
----------------
----------------


Year: Friday
Berks Winning: BinomTestResult(k=929, n=170

In [447]:
stats_df_berks

N_races  Berks_wins  Statistic       p_value
all_races                          7556.0      4044.0   0.535204  4.945864e-10
all_international_v_uk_races       2985.0      1542.0   0.516583  3.642031e-02
weekend_international_v_uk_races    672.0       355.0   0.528274  7.671943e-02
all_weekend_races                  1548.0       863.0   0.557494  3.343914e-06
1999                                284.0       163.0   0.573944  7.416341e-03
2000                                285.0       156.0   0.547368  6.169187e-02
2001                                281.0       165.0   0.587189  2.054846e-03
2002                                269.0       149.0   0.553903  4.379920e-02
2003                                294.0       171.0   0.581633  3.014481e-03
2004                                268.0       124.0   0.462687  9.002602e-01
2005                                278.0       136.0   0.489209  6.626578e-01
2006                                270.0       145.0   0.537037  1.237543e-01
2007                                285.0       155.0   0.543860  7.750426e-02
2008                                277.0       146.0   0.527076  2.001451e-01
2009                                281.0       142.0   0.505338  4.525288e-01
2010                                292.0       156.0   0.534247  1.330767e-01
2011                                283.0       146.0   0.515901  3.172361e-01
2012                                293.0       154.0   0.525597  2.067327e-01
2013                                280.0       153.0   0.546429  6.751160e-02
2014                                286.0       155.0   0.541958  8.685891e-02
2015                                287.0       144.0   0.501742  5.000000e-01
2016                                304.0       162.0   0.532895  1.379051e-01
2017                                309.0       157.0   0.508091  4.100200e-01
2018                                306.0       185.0   0.604575  1.511076e-04
2019                                330.0       190.0   0.575758  3.449620e-03
2021                                319.0       157.0   0.492163  6.315107e-01
2022                                393.0       200.0   0.508906  3.810968e-01
2023                                394.0       221.0   0.560914  8.890586e-03
2024                                408.0       212.0   0.519608  2.288795e-01
Tuesday                             242.0       134.0   0.553719  5.392443e-02
Wednesday                          2022.0      1064.0   0.526212  9.758853e-03
Thursday                           2035.0      1054.0   0.517936  5.522597e-02
Friday                             1709.0       929.0   0.543593  1.704010e-04
Saturday                           1027.0       577.0   0.561831  4.135949e-05
Sunday                              521.0       286.0   0.548944  1.419428e-02

In [448]:
stats_df_intl

N_races  International_on_bucks  Statistic  \
all_international_v_uk_races       2985.0                  1530.0   0.512563   
weekend_international_v_uk_races    672.0                   330.0   0.491071   
1999                                114.0                    60.0   0.526316   
2000                                 92.0                    49.0   0.532609   
2001                                119.0                    66.0   0.554622   
2002                                104.0                    45.0   0.432692   
2003                                131.0                    71.0   0.541985   
2004                                117.0                    57.0   0.487179   
2005                                109.0                    58.0   0.532110   
2006                                 78.0                    48.0   0.615385   
2007                                108.0                    52.0   0.481481   
2008                                 99.0                    53.0   0.535354   
2009                                112.0                    63.0   0.562500   
2010                                119.0                    52.0   0.436975   
2011                                118.0                    61.0   0.516949   
2012                                102.0                    57.0   0.558824   
2013                                 92.0                    45.0   0.489130   
2014                                114.0                    55.0   0.482456   
2015                                124.0                    62.0   0.500000   
2016                                131.0                    72.0   0.549618   
2017                                132.0                    69.0   0.522727   
2018                                125.0                    62.0   0.496000   
2019                                165.0                    86.0   0.521212   
2021                                 50.0                    26.0   0.520000   
2022                                165.0                    71.0   0.430303   
2023                                182.0                   100.0   0.549451   
2024                                183.0                    90.0   0.491803   
Tuesday                              81.0                    39.0   0.481481   
Wednesday                           640.0                   345.0   0.539062   
Thursday                            833.0                   422.0   0.506603   
Friday                              759.0                   394.0   0.519104   
Saturday                            437.0                   211.0   0.482838   
Sunday                              235.0                   119.0   0.506383   

                                   p_value  
all_international_v_uk_races      0.087793  
weekend_international_v_uk_races  0.691969  
1999                              0.319885  
2000                              0.301206  
2001                              0.135624  
2002                              0.929522  
2003                              0.191177  
2004                              0.644148  
2005                              0.282850  
2006                              0.026772  
2007                              0.684683  
2008                              0.273357  
2009                              0.109566  
2010                              0.928934  
2011                              0.391278  
2012                              0.138007  
2013                              0.622674  
2014                              0.680115  
2015                              0.535754  
2016                              0.147203  
2017                              0.331793  
2018                              0.570940  
2019                              0.320281  
2021                              0.443862  
2022                              0.969311  
2023                              0.103752  
2024                              0.616219  
Tuesday                           0.671504  
Wednesda

In [450]:
stats_df_berks.to_csv('station_win_stats.csv',index=True)
stats_df_intl.to_csv('station_placement_stats.csv',index=True)

## Margin Analysis

In [492]:
df['verdict'][0:20]

0         1 Length
1       4¾ Lengths
2        3 Lengths
3       2¼ Lengths
4         ½ Length
5       2¼ Lengths
6         ½ Length
7       2½ Lengths
8     Sculled over
9       1¼ Lengths
10      3¼ Lengths
11        1 Length
12      3½ Lengths
13        ⅓ Length
14        ¾ Length
15        ¾ Length
16      4½ Lengths
17      4½ Lengths
18        ½ Length
19      3¾ Lengths
Name: verdict, dtype: object

In [514]:
def fraction_to_float(fraction):
    if fraction.isdigit():
        return float(fraction)
    elif '/' in fraction:
        numerator, denominator = fraction.split('/')
        return float(numerator) / float(denominator)
    elif '¼' in fraction:
        return 0.25
    elif '⅓' in fraction:
        return (1/3)
    elif '½' in fraction:
        return 0.5
    elif '⅔' in fraction:
        return (2/3)
    elif '¾' in fraction:
        return 0.75
    else:
        return 0

def convert_to_feet(value):
    if "Easily" in value:
        return 5.5 * 40  # 5.5 lengths * 40 feet per length
    elif "Feet" in value:
        return float(re.findall(r'\d+', value)[0])
    else:
        parts = re.findall(r'\d*\s*\d*[½⅓⅔¼¾]|\d+/\d+|\d+', value)
        if parts == []:
            return(0)
        else:
            if len(parts[0]) == 2:  # For cases like "120 3¼" or "131 ½"
                return (fraction_to_float(parts[0][0]) + fraction_to_float(parts[0][1])) * 40
            elif len(parts) == 1:
                return fraction_to_float(parts[0]) * 40
            else:
                return 0  # Default value if no match found
    
def feet_to_length(value):
    print(value)
    lengths = value/40
    return (lengths)

# Apply the conversion function and round to nearest integer
df['norm_verdict'] = df['verdict'].apply(convert_to_feet).round().astype(int).apply(feet_to_length)

40
190
120
90
20
90
20
100
0
50
130
40
140
13
30
30
180
180
20
150
27
130
110
220
110
80
40
150
40
200
110
27
30
80
90
220
220
27
110
220
190
220
140
130
80
90
110
13
50
160
10
100
90
40
190
40
70
70
60
140
20
100
220
190
0
220
220
130
220
220
220
220
220
100
190
0
120
60
120
27
90
140
3
13
220
220
140
120
220
220
220
60
170
140
150
2
80
130
180
100
27
120
100
80
10
60
220
50
100
200
100
40
220
60
150
20
13
0
120
60
130
200
60
30
60
220
220
120
220
220
220
20
220
220
220
130
220
40
220
4
220
220
100
80
70
80
220
180
90
90
220
50
50
30
170
70
220
220
220
220
220
170
220
40
160
220
90
30
27
120
80
100
220
90
13
140
40
80
220
50
50
110
220
27
50
100
50
100
140
190
40
60
60
120
170
220
220
90
40
70
70
100
27
0
100
220
220
220
80
220
20
120
100
200
220
80
10
40
90
40
30
27
130
110
110
180
30
110
140
20
20
180
30
180
80
170
30
27
100
20
80
220
150
120
180
190
40
40
50
220
60
130
110
50
190
220
50
60
50
70
220
80
90
220
120
120
100
120
30
6
100
60
140
220
20
60
60
70
30
200
6
120
130
160
20
2

In [513]:
df['norm_verdict'][0:20]

0     1.000
1     4.750
2     3.000
3     2.250
4     0.500
5     2.250
6     0.500
7     2.500
8     0.000
9     1.250
10    3.250
11    1.000
12    3.500
13    0.325
14    0.750
15    0.750
16    4.500
17    4.500
18    0.500
19    3.750
Name: norm_verdict, dtype: float64